## Generating the Supply Surface

This notebook walks through the process we've taken to generate the Supply Surface over the UK.

### Underground Workings

We have assumed that any land within 250m of the underground workings *may* sit above a source of mine water. By adding this buffer, we have accounted for any uncertainty in the underground workings data.

We have also set a 10km buffer around the mine workings as the total area to consider for all things related to potential mine water heating schemes. 

In [14]:
import pandas as pd
import geopandas as gpd

from tqdm.notebook import tqdm
from shapely.ops import unary_union

# Load the underground workings polygon data
underground_workings = gpd.read_file("supply_data/underground_workings_outline.geojson").simplify(100)

# Create a 250m buffer around the underground workings to account for uncertainty
underground_workings_250m_buffer = unary_union(underground_workings.buffer(250))

# Create a 10_000m buffer around the underground workings to act as a base to work off of
underground_workings_10_000m_buffer = unary_union(underground_workings.buffer(10000))

### Mine Water Treatment Sites

For the bolt-on archetype, we need data on the locations of mine water treatment sites as well as ***Flow Rates*** and ***Water Temps*** for each site.

Data provided by the TCA gives us most of this information for both existing and proposed treatment sites, however none of the proposed treatment sites had an estimate for *Water Temp*, and some sites only had partial data available. We could have excluded these sites from the supply surface, however we decided it would be better to make some reasonable estimates for the missing values instead. We did this by calculating the average values of *Flow Rate* and *Water Temp* across all sites which that data was available for. 

For sites missing:
* Flow-rate data, we have used ~ 46 L/s.
* Water-temperature data, we have used ~ 13°C.

Then, we calculate a ***Flow Index*** and a ***Temp Index*** for each site by dividing its *Flow Rate* and *Water Temp* values by the average values above. These indexes tell us how a site compares to the average site, i.e. a site with a *Flow Index* of 2.0 has twice the *Flow Rate* of the average site.

Finally, we calculate the ***Supply Score*** by multiplying the *Flow Index* and *Temp Index* together.

In [15]:
treatment_sites = "supply_data/ExistingAndProposedMineWaterTreatmentSiteData.xlsx"
treatment_sites = pd.read_excel(treatment_sites)

average_flow_rate = treatment_sites["Flow Rate"].mean()
average_water_temp = treatment_sites["Water Temp"].mean()

# Filling in missing Flow Rate and Water Temp values with the average values.
treatment_sites["Flow Rate"] = treatment_sites["Flow Rate"].fillna(average_flow_rate)
treatment_sites["Water Temp"] = treatment_sites["Water Temp"].fillna(average_water_temp)

# Calculating Flow Index, Temp Index and Supply Score
treatment_sites["Flow Index"] = treatment_sites["Flow Rate"] / average_flow_rate
treatment_sites["Temp Index"] = treatment_sites["Water Temp"] / average_water_temp
treatment_sites["Supply Score"] = treatment_sites["Flow Index"].mul(treatment_sites["Temp Index"])

### Assigning Supply Scores to H3 Cells

H3 is an initiative lead by Uber for indexing geographies into a hexagonal grid. We are using this hexagonal grid as our basis for discretising the UK.

Here we have used resolution level 9 (L9) hexagons, which have a total area of about 0.1km^2 and a side length of about 200m.
Note: For visualisation purposed, I've switched to L7 hexagons, total area ~ 5km^2, side length ~ 1.4km

To make the supply surface:
1. Add every cell within 10km of the underground workings polygon to a list
2. For every cell within 250m of the underground workings polygon, mark that cell with ***UndergroundWorkingsPresent = True***
3. Identify the cells that contain mine water treatment sites and mark those cells with ***TreatmentSitePresent = True***
4. Save all the cells to a file, along with any treatment site properties that are relevant. 

In [21]:
from h3 import geo_to_cells, latlng_to_cell, cells_to_geo
from pyproj import Transformer
from shapely.ops import transform
from shapely import from_geojson, Point
from orjson import dumps

# Set the resolution level and create a tool to convert eastings and northings into latitudes and longitudes
RES = 7
BNG_to_WGS = Transformer.from_crs(27700, 4326, always_xy=True)

# 1. Add every cell within 10km of the underground workings polygon to a list
h3britain = set()
for g in tqdm(underground_workings_10_000m_buffer.geoms):
    h3britain.update(geo_to_cells(transform(BNG_to_WGS.transform, g).__geo_interface__, RES))

# 2. For every cell within 250m of the underground workings polygon, mark that cell with UndergroundWorkingsPresent = True
h3underground_workings = set()
for g in tqdm(underground_workings_250m_buffer.geoms):
    h3underground_workings.update(geo_to_cells(transform(BNG_to_WGS.transform, g).__geo_interface__, RES))

# 3. Identify the cells that contain mine water treatment sites and mark those cells with TreatmentSitePresent = True
h3treatment_sites = {}
for index, site in tqdm(treatment_sites.iterrows(), total=len(treatment_sites.index)):
    g = Point([site["Easting"], site["Northing"]])
    g = transform(BNG_to_WGS.transform, g)

    cell_ref = latlng_to_cell(lat=g.y, lng=g.x, res=RES)
    if cell_ref not in h3treatment_sites:
        h3treatment_sites[cell_ref] = site
    else:
        raise Exception()

# 4. Save all the cells to a file, along with any treatments site properties that are relevant.
treatment_site_data = [h3treatment_sites[cell] if cell in h3treatment_sites else None for cell in h3britain]
supply_surface = gpd.GeoDataFrame(index=list(h3britain), data={
    "geometry": [from_geojson(dumps(cells_to_geo([hex]))) for hex in h3britain],
    "Bolt-on Supply Score": [0 if site is None else site.get("Supply Score", None) for site in treatment_site_data],
    "Borehole Supply Score": [1 if cell in h3underground_workings else 0 for cell in h3britain],
    "UndergroundWorkingsPresent": [cell in h3underground_workings for cell in h3britain],
    "TreatmentSitePresent": [False if site is None else True for site in treatment_site_data],
    "TreatmentSiteProposed": [None if site is None else site.get("Proposed", None) for site in treatment_site_data],
    "TreatmentSiteName": [None if site is None else site.get("Site Name", None) for site in treatment_site_data],
    "TreatmentSiteOperational": [None if site is None else site.get("Operational", None) for site in treatment_site_data],
    "TreatmentSiteType": [None if site is None else site.get("Treatment\nType", None) for site in treatment_site_data],
    "TreatmentSitePumped": [None if site is None else site.get("Pumped\n(Y/N)", None) for site in treatment_site_data],
    "TreatmentSiteFlow (L/s)": [None if site is None else site.get("Flow or Pumping Rate (L/s)", None) for site in treatment_site_data],
    "TreatmentSiteFlowIndex": [None if site is None else site.get("Flow Index", None) for site in treatment_site_data],
    "TreatmentSiteTemperature (°C)": [None if site is None else site.get("Temperature\n(˚C)", None) for site in treatment_site_data],
    "TreatmentSiteTempIndex": [None if site is None else site.get("Temp Index", None) for site in treatment_site_data],
    "TreatmentSiteHeatPotential": [None if site is None else site.get("Heat Potential\n(MW)", None) for site in treatment_site_data],
}, crs="EPSG:4326").set_geometry("geometry")

supply_surface.head()
supply_surface.to_excel(f"outputs/supply_surface_res_{RES}.xlsx")
supply_surface.to_file(f"outputs/supply_surface_res_{RES}.gpkg", driver="GPKG")

  0%|          | 0/16 [00:00<?, ?it/s]

  0%|          | 0/678 [00:00<?, ?it/s]

  0%|          | 0/120 [00:00<?, ?it/s]

### Visualisation

On a map, paint every cell with a treatment site on it red, and every cell thats within 250m of underground workings blue.

In [23]:
import folium

map = folium.Map(location=[53.15, -1.2], tiles="CartoDB Positron", zoom_start=9)
    
def set_style(x):

    if x["properties"]["TreatmentSitePresent"]:
        color = "red"
        opacity = 0.5
    elif x["properties"]["UndergroundWorkingsPresent"]:
        color = "blue"
        opacity = 0.2
    else: 
        color = "green"
        opacity = 0
    
    return {
        "color": color,
        "opacity": opacity,
        "fillColor": color,
        "fillOpacity": opacity
    }

for feat in supply_surface.iterfeatures():

    if not feat["properties"]["TreatmentSitePresent"] and not feat["properties"]["UndergroundWorkingsPresent"]:
        continue

    feat["geometry"] = from_geojson(dumps(feat["geometry"])).simplify(tolerance=0.001).__geo_interface__

    geo_j = folium.GeoJson(data=feat,
                           style_function=lambda x: set_style(x))

    geo_j.add_to(map)

map